<a href="https://colab.research.google.com/github/FelipeSotoG/Desafio-Final/blob/main/Desafio_Final.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Boxing usando Actor Crítico (PPO)
Basado en [este algoritmo](https://keras.io/examples/rl/ppo_cartpole/)

Instalamos paquetes necesarios

Se esta instalando Autorom, esto nos deja tener acceso a varios roms de atari para importarlos a retro.

In [1]:
!pip install gym[atari]
!pip install autorom[accept-rom-license]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
  Created wheel for AutoROM.accept-rom-license: filename=AutoROM.accept_rom_license-0.4.2-py3-none-any.whl size=441027 sha256=c7fbb6c43cd97de6f160a8056a8d4539907f4d60dbc2bb31d04ede663e0abb3c
  Stored in directory: /root/.cache/pip/wheels/87/67/2e/6147e7912fe37f5408b80d07527dab807c1d25f5c403a9538a
Successfully built AutoROM.accept-rom-license


Se tiene que mover los rom que estan en formato ".bin" estos estan en el directorio de python por lo cual podemos sacarlos directamente.

In [2]:
!mv /usr/local/lib/python3.7/dist-packages/AutoROM/roms/*.bin /content

In [3]:
!pip install gym-retro > /dev/null 2>&1 
!python3 -m retro.import .  > /dev/null 2>&1 

## Librerías necesarias

In [4]:
import numpy as np
import tensorflow as tf
from tensorflow import keras
from keras import layers
import gym
import scipy.signal
import time

## Parámetros del algoritmo

In [5]:
n_frames= 10
steps_per_epoch = 720
epochs = 50
ratio = 0.1
hidden_sizes = (64, 64)
policy_learning_rate = 3e-4
value_function_learning_rate = 1e-3
train_policy_iterations = 80
train_value_iterations = 80
clip_ratio = 0.2
gamma = 0.99
lam = 0.97
target_kl = 0.01


se uso 1000 steps y 10 epochs por razones de tiempo

#Modelo con convoluciones

Funciones para interactuar con ambiente

Se encapsulan las funciones del ambiente para realizar un par de modificaciones:

- `env_step`: Permite repetir la acción por `iters` frames y retorna el stacked state resultante junto a la recompensa acumulada de los 5 frames. Esto permite que los episodios se realicen más rápidamente. Además, el episodio termina al perder la primera vida.

- `env_reset`: Además de resetear el ambiente, avanza 10 iteraciones para dar el primer paso.

In [50]:
def env_reset(env, iter=5):
  env.reset()
  state, reward, done, _ = env_step(env, 0, iters=iter, new_episode=True) #starting
  return state

images = None

import tensorflow as tf
def env_step(env, action, iters=5, new_episode=False, show=False):
  reward=0
  action = possible_actions[action]
  auxim = np.zeros((iters,size[0],size[1],size[2]))
  for i in range(iters):
    obs, r, done, info = env.step(action)
    auxim[i]=obs
    obs=tf.image.resize(obs,(140,80))
    reward+=r
    if done: break
  if(show): images.append(obs)
  state = stacked_state(obs,new_episode)
  
  return state, reward, done, auxim

Buffer para convolucion

In [7]:
class Buffer:
    # Buffer for storing trajectories
    def __init__(self, observation_dimensions, size, gamma=0.99, lam=0.95):
        # Buffer initialization
        self.observation_buffer = np.zeros(
            (size,observation_dimensions[0],observation_dimensions[1],observation_dimensions[2]), dtype=np.float32
        )
        self.action_buffer = np.zeros(size, dtype=np.int32)
        self.advantage_buffer = np.zeros(size, dtype=np.float32)
        self.reward_buffer = np.zeros(size, dtype=np.float32)
        self.return_buffer = np.zeros(size, dtype=np.float32)
        self.value_buffer = np.zeros(size, dtype=np.float32)
        self.logprobability_buffer = np.zeros(size, dtype=np.float32)
        self.gamma, self.lam = gamma, lam
        self.pointer, self.trajectory_start_index = 0, 0

    def store(self, observation, action, reward, value, logprobability):
        # Append one step of agent-environment interaction
        self.observation_buffer[self.pointer] = observation
        self.action_buffer[self.pointer] = action
        self.reward_buffer[self.pointer] = reward
        self.value_buffer[self.pointer] = value
        self.logprobability_buffer[self.pointer] = logprobability
        self.pointer += 1

    def finish_trajectory(self, last_value=0):
        # Finish the trajectory by computing advantage estimates and rewards-to-go
        path_slice = slice(self.trajectory_start_index, self.pointer)
        rewards = np.append(self.reward_buffer[path_slice], last_value)
        values = np.append(self.value_buffer[path_slice], last_value)

        deltas = rewards[:-1] + self.gamma * values[1:] - values[:-1]

        self.advantage_buffer[path_slice] = discounted_cumulative_sums(
            deltas, self.gamma * self.lam
        )
        self.return_buffer[path_slice] = discounted_cumulative_sums(
            rewards, self.gamma
        )[:-1]

        self.trajectory_start_index = self.pointer

    def get(self):
        # Get all data of the buffer and normalize the advantages
        self.pointer, self.trajectory_start_index = 0, 0
        advantage_mean, advantage_std = (
            np.mean(self.advantage_buffer),
            np.std(self.advantage_buffer),
        )
        self.advantage_buffer = (self.advantage_buffer - advantage_mean) / advantage_std
        return (
            self.observation_buffer,
            self.action_buffer,
            self.advantage_buffer,
            self.return_buffer,
            self.logprobability_buffer,
        )

In [8]:
def discounted_cumulative_sums(x, discount):
    # Discounted cumulative sums of vectors for computing rewards-to-go and advantage estimates
    return scipy.signal.lfilter([1], [1, float(-discount)], x[::-1], axis=0)[::-1]



def logprobabilities(logits, a):
    # Compute the log-probabilities of taking actions a by using the logits (i.e. the output of the actor)
    logprobabilities_all = tf.nn.log_softmax(logits)
    logprobability = tf.reduce_sum(
        tf.one_hot(a, num_actions) * logprobabilities_all, axis=1
    )
    return logprobability


# Sample action from actor
@tf.function
def sample_action(observation):
    logits = actor(observation)
    action = tf.squeeze(tf.random.categorical(logits, 1), axis=1)
    return logits, action


Función para "stackear" frames

Para que el agente entienda la velocidad y movimiento de los objetos, consideramos que un estado considera un **conjunto de observaciones** y no sólo la última retornada por el ambiente.

La función `stacked_state` mantiene un estado compuesto por los últimos `n_frames=10` estados, es mas que antes por limitaciones de dimensiones. Este será el estado que observe el agente.

In [9]:
from collections import deque

stacked_frames = None

def stacked_state(state, is_new_episode):  
    global stacked_frames
    if is_new_episode or stacked_frames==None:

        # Clear our stacked_frames
        stacked_frames = deque([np.zeros((observation_dimensions), dtype=np.int) for i in range(n_frames)], maxlen=n_frames)  
        # Because we're in a new episode, copy the same frame 4x
        for i in range(n_frames):
          stacked_frames.append(state)
        
        # Stack the state
        stacked_state = np.concatenate(stacked_frames, axis=2)
        
    else:
        # Append frame to deque, automatically removes the oldest frame
        if state is not None: stacked_frames.append(state)
        else: stacked_frames.append(np.zeros(observation_dimensions, dtype=np.int))

        # Build the stacked state (first dimension specifies different frames)
        stacked_state = np.concatenate(stacked_frames, axis=2) 
    
    return stacked_state

Convolution version

Este es un bloque de convolucion basado en Resnet

<img src="https://external-content.duckduckgo.com/iu/?u=https%3A%2F%2Fwww.jeremyjordan.me%2Fcontent%2Fimages%2F2018%2F04%2FScreen-Shot-2018-04-16-at-5.47.38-PM.png&f=1&nofb=1)" width=500px>

In [33]:
def conv_block(X,f,d=0.1):
  c = tf.keras.layers.Conv2D(f[0], (1, 1), activation='relu', kernel_initializer='he_normal', padding='same')(X)
  c = tf.keras.layers.BatchNormalization(axis=3)(c)
  c = tf.keras.layers.Dropout(d)(c)
  c = tf.keras.layers.Conv2D(f[1], (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c)
  c = tf.keras.layers.BatchNormalization(axis=3)(c)
  c = tf.keras.layers.Dropout(d)(c)
  c = tf.keras.layers.Conv2D(f[2], (1, 1), kernel_initializer='he_normal', padding='same')(c)
  c = tf.keras.layers.BatchNormalization(axis=3)(c)
  s = tf.keras.layers.Conv2D(f[2], (1, 1), kernel_initializer='he_normal', padding='same')(X)
  s = tf.keras.layers.BatchNormalization(axis=3)(s)
  c = tf.keras.layers.Add()([s,c])
  c = tf.keras.layers.ReLU()(c)
  return c

Este es un bloque de convolucion basado en Unet
![image](https://www.researchgate.net/publication/341300084/figure/fig4/AS:890174032580608@1589245436074/The-proposed-U-net-architecture.png)

In [11]:
def conv_block(X,f,d=0.1):
  c = tf.keras.layers.Conv2D(f[0], (2, 2), activation='relu', kernel_initializer='he_normal', padding='same')(X)
  c = tf.keras.layers.Dropout(d)(c)
  c = tf.keras.layers.Conv2D(f[1], (2, 2), activation='relu', kernel_initializer='he_normal', padding='same')(c)
  c = tf.keras.layers.Dropout(d)(c)
  return c

Aqui se listan los juegos que podemos usar:

In [14]:
for game in retro.data.list_games():
   print(game)

1942-Nes
1943-Nes
3NinjasKickBack-Genesis
8Eyes-Nes
AaahhRealMonsters-Genesis
AbadoxTheDeadlyInnerWar-Nes
AcceleBrid-Snes
ActRaiser2-Snes
ActionPachio-Snes
AddamsFamily-GameBoy
AddamsFamily-Genesis
AddamsFamily-Nes
AddamsFamily-Sms
AddamsFamily-Snes
AddamsFamilyPugsleysScavengerHunt-Nes
AddamsFamilyPugsleysScavengerHunt-Snes
AdvancedBusterhawkGleylancer-Genesis
Adventure-Atari2600
AdventureIsland-GameBoy
AdventureIsland3-Nes
AdventureIslandII-Nes
AdventuresOfBatmanAndRobin-Genesis
AdventuresOfBayouBilly-Nes
AdventuresOfDinoRiki-Nes
AdventuresOfDrFranken-Snes
AdventuresOfKidKleets-Snes
AdventuresOfMightyMax-Genesis
AdventuresOfMightyMax-Snes
AdventuresOfRockyAndBullwinkleAndFriends-Genesis
AdventuresOfRockyAndBullwinkleAndFriends-Nes
AdventuresOfRockyAndBullwinkleAndFriends-Snes
AdventuresOfStarSaver-GameBoy
AdventuresOfYogiBear-Snes
AeroFighters-Snes
AeroStar-GameBoy
AeroTheAcroBat-Snes
AeroTheAcroBat2-Genesis
AeroTheAcroBat2-Snes
AfterBurnerII-Genesis
AfterBurst-GameBoy
AirBuster-Gene

In [51]:
import gym
import retro
# Initialize the environment and get the dimensionality of the
# observation space and the number of possible actions
# Create our environment

if 'env' in locals(): env.close()
#env = gym.make('Boxing-v4')
#env = gym.make('ALE/Boxing-v5')
#env = retro.make(game='Solaris-Atari2600')
#env = retro.make(game='Boxing-Atari2600')
#env = retro.make(game='PrivateEye-Atari2600')
#env = retro.make(game='Frostbite-Atari2600')
#env = retro.make(game='CrazyClimber-Atari2600')
env = retro.make(game='Bowling-Atari2600')

size=env.observation_space.shape
#observation_dimensions = 14*n_frames # 14 objects
#observation_dimensions = (size[0], size[1], size[2]*n_frames)
observation_dimensions = (140,80, 3*n_frames)
num_actions = env.action_space.n
possible_actions = np.array(np.identity(num_actions,dtype=int).tolist())


print("The size of our frame is: ", env.observation_space)

# Here we create an hot encoded version of our actions
# possible_actions = [[1, 0, 0, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0, 0, 0]...]
possible_actions = np.array(np.identity(num_actions,dtype=int).tolist())


def mlp(x, sizes, activation=tf.tanh, output_activation=None):    
    # Build a feedforward neural network
    for size in sizes[:-1]:
        x = layers.Dense(units=size, activation=activation)(x)
    return layers.Dense(units=sizes[-1], activation=output_activation)(x)

# Train the policy by maxizing the PPO-Clip objective
@tf.function
def train_policy(
    observation_buffer, action_buffer, logprobability_buffer, advantage_buffer
):

    with tf.GradientTape() as tape:  # Record operations for automatic differentiation.
        ratio = tf.exp(
            logprobabilities(actor(observation_buffer), action_buffer)
            - logprobability_buffer
        )
        min_advantage = tf.where(
            advantage_buffer > 0,
            (1 + clip_ratio) * advantage_buffer,
            (1 - clip_ratio) * advantage_buffer,
        )

        policy_loss = -tf.reduce_mean(
            tf.minimum(ratio * advantage_buffer, min_advantage)
        )
    policy_grads = tape.gradient(policy_loss, actor.trainable_variables)
    policy_optimizer.apply_gradients(zip(policy_grads, actor.trainable_variables))

    kl = tf.reduce_mean(
        logprobability_buffer
        - logprobabilities(actor(observation_buffer), action_buffer)
    )
    kl = tf.reduce_sum(kl)
    return kl


# Train the value function by regression on mean-squared error
@tf.function
def train_value_function(observation_buffer, return_buffer):
    with tf.GradientTape() as tape:  # Record operations for automatic differentiation.
        value_loss = tf.reduce_mean((return_buffer - critic(observation_buffer)) ** 2)
    value_grads = tape.gradient(value_loss, critic.trainable_variables)
    value_optimizer.apply_gradients(zip(value_grads, critic.trainable_variables))

# Topologia de convolucion basada en parte por resnet50 y Unet

observation_input = keras.Input(shape=(observation_dimensions), dtype=tf.float32)


c1 = conv_block(observation_input,(16,16,32))
c1 = tf.keras.layers.MaxPooling2D((2, 2))(c1)
c2 = conv_block(c1,(32,32,64),d=0.2)
c2 = tf.keras.layers.MaxPooling2D((2, 2))(c2)
c3 = conv_block(c2,(64,64,128),d=0.3)
c3 = tf.keras.layers.MaxPooling2D(pool_size=(2, 2))(c3)
c3 = tf.keras.layers.GlobalAveragePooling2D()(c3)
"""
c1 = conv_block(observation_input,(8,8))
c1 = tf.keras.layers.MaxPooling2D((2, 2))(c1)
c2 = conv_block(c1,(16,16),d=0.2)
c2 = tf.keras.layers.MaxPooling2D((2, 2))(c2)
c3 = conv_block(c2,(32,32),d=0.3)
c3 = tf.keras.layers.MaxPooling2D(pool_size=(2, 2))(c3)
c3 = tf.keras.layers.GlobalAveragePooling2D()(c3)
"""
# Initialize the actor and the critic as keras models
logits = mlp(c3, list(hidden_sizes) + [num_actions], tf.tanh, None)
actor = keras.Model(inputs=observation_input, outputs=logits)
value = mlp(c3, list(hidden_sizes) + [1], tf.tanh, None)

critic = keras.Model(inputs=observation_input, outputs=value)

# Initialize the policy and the value function optimizers
policy_optimizer = keras.optimizers.Adam(learning_rate=policy_learning_rate)
value_optimizer = keras.optimizers.Adam(learning_rate=value_function_learning_rate)

The size of our frame is:  Box(0, 255, (210, 160, 3), uint8)


In [39]:
actor.summary()

Model: "model_8"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_5 (InputLayer)           [(None, 100, 80, 30  0           []                               
                                )]                                                                
                                                                                                  
 conv2d_30 (Conv2D)             (None, 100, 80, 16)  496         ['input_5[0][0]']                
                                                                                                  
 batch_normalization_12 (BatchN  (None, 100, 80, 16)  64         ['conv2d_30[0][0]']              
 ormalization)                                                                                    
                                                                                            

Entrenamiento (AC3)

El entrenamiento consiste en lo siguiente:

- Se recolectan datos para entrenar modelos
<estado, acción, recompensa>. Estos datos son guardados en el buffer 

- Para la recolección de datos, se sigue política softmax usando predicciones del actor.

- Al terminar un episodio, se calculan retornos y advantages para cada estado. Advantages son calculados usando crítico .

- Se ajustan los modelos:
  
  - Crítico predice retorno esperado a partir de cada estado. 
  - Actor predice advantages para cada estado-acción.

- Se repite todo el proceso.

![image](https://i.imgur.com/rd5tda1.png)

In [52]:
# Initialize the buffer
buffer = Buffer(observation_dimensions, steps_per_epoch)

# Initialize the observation, episode return and episode length
observation, episode_return, episode_length = env_reset(env), 0, 0

# Iterate over the number of epochs
for epoch in range(epochs):
    # Initialize the sum of the returns, lengths and number of episodes for each epoch
    sum_return = 0;   sum_length = 0;   num_episodes = 0;   episode_max_return = 0
    auxim= None
    # Iterate over the steps of each epoch
    for t in range(steps_per_epoch):
        observation=observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2]))
        # Get the logits, action, and take one step in the environment
        logits, action = sample_action(observation)
        observation_new, reward, done, _ = env_step(env, action[0].numpy(), iters=10)
        episode_return += reward
        episode_length += 1

        # Get the value and log-probability of the action
        value_t = critic(observation)
        logprobability_t = logprobabilities(logits, action)
        # Store obs, act, rew, v_t, logp_pi_t
        buffer.store(observation, action, reward, value_t, logprobability_t,)
        # Update the observation
        observation = observation_new
        # Finish trajectory if reached to a terminal state
        terminal = done
        if terminal or (t == steps_per_epoch - 1):
            last_value = 0 if done else critic(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
            buffer.finish_trajectory(last_value)
            sum_return += episode_return
            sum_length += episode_length
            num_episodes += 1
            if episode_return > episode_max_return: episode_max_return=episode_return
            observation, episode_return, episode_length = env_reset(env), 0, 0 
            
    # Get values from the buffer
    (
        observation_buffer,
        action_buffer,
        advantage_buffer,
        return_buffer,
        logprobability_buffer,
    ) = buffer.get()

    # Update the policy and implement early stopping using KL divergence
    for _ in range(train_policy_iterations):
        kl = train_policy(
            observation_buffer, action_buffer, logprobability_buffer, advantage_buffer
        )
        if kl > 1.5 * target_kl:
            # Early Stopping
            break

    # Update the value function
    for _ in range(train_value_iterations):
        train_value_function(observation_buffer, return_buffer)

    # Print mean return and length for each epoch
    print(
        f" Epoch: {epoch + 1}. MeanReturn: {sum_return / num_episodes}. MeanLength: {sum_length / num_episodes}. MaxReturn: {episode_max_return}"
    )

 Epoch: 1. MeanReturn: 21.0. MeanLength: 720.0. MaxReturn: 21.0
 Epoch: 2. MeanReturn: 8.0. MeanLength: 720.0. MaxReturn: 8.0
 Epoch: 3. MeanReturn: 26.0. MeanLength: 720.0. MaxReturn: 26.0
 Epoch: 4. MeanReturn: 19.0. MeanLength: 720.0. MaxReturn: 19.0
 Epoch: 5. MeanReturn: 21.0. MeanLength: 720.0. MaxReturn: 21.0
 Epoch: 6. MeanReturn: 6.0. MeanLength: 720.0. MaxReturn: 6.0
 Epoch: 7. MeanReturn: 26.0. MeanLength: 720.0. MaxReturn: 26.0
 Epoch: 8. MeanReturn: 15.0. MeanLength: 720.0. MaxReturn: 15.0
 Epoch: 9. MeanReturn: 15.0. MeanLength: 720.0. MaxReturn: 15.0
 Epoch: 10. MeanReturn: 14.0. MeanLength: 720.0. MaxReturn: 14.0
 Epoch: 11. MeanReturn: 42.0. MeanLength: 720.0. MaxReturn: 42.0
 Epoch: 12. MeanReturn: 20.0. MeanLength: 720.0. MaxReturn: 20.0
 Epoch: 13. MeanReturn: 3.0. MeanLength: 720.0. MaxReturn: 3.0
 Epoch: 14. MeanReturn: 8.0. MeanLength: 720.0. MaxReturn: 8.0
 Epoch: 15. MeanReturn: 12.0. MeanLength: 720.0. MaxReturn: 12.0
 Epoch: 16. MeanReturn: 16.0. MeanLength: 

Se instalan las librerias para la creacion del video

In [ ]:
# Librearías requeridas
!apt-get install x11-utils > /dev/null 2>&1 
!pip install pyglet > /dev/null 2>&1 
!apt-get install -y xvfb python-opengl > /dev/null 2>&1
!pip install gym pyvirtualdisplay > /dev/null 2>&1

#Primera Simulacion Env reset con 10 iteraciones de entrada

### Simulación

In [ ]:
episode_return=0.0
i=0
while episode_return < 2:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, _ = env_step(env, action[0].numpy(), iters=10, show=True)

      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env)
        print(episode_return)
        break
  i+=1
episode_return

-13.0
-14.0
-41.0
-29.0
-9.0
-7.0
-1.0
-32.0
-41.0
-11.0
0.0
-23.0
-7.0
-8.0
-13.0
2.0


2.0

In [ ]:
episode_return=0.0
i=0
while episode_return < 1 and i<10:
  observation, episode_return, episode_length = env_reset(env), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, _ = env_step(env, action[0].numpy(), iters=10, show=True)

      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env)
        print(episode_return)
        break
  i+=1
episode_return

1.0

In [ ]:
episode_return=0.0
i=0
while episode_return < 2:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, _ = env_step(env, action[0].numpy(), iters=10, show=True)

      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env)
        print(episode_return)
        break
  i+=1
episode_return

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  # Remove the CWD from sys.path while we load stuff.


-28.0
-21.0
-47.0
-32.0
-13.0
-2.0
-35.0
-7.0
-6.0
-24.0
-15.0
-2.0
-18.0
-25.0
-26.0
-16.0
-26.0
-2.0
-13.0
-13.0
-22.0
-9.0
2.0


2.0

In [ ]:
episode_return=0.0
i=0
while episode_return < 1:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, _ = env_step(env, action[0].numpy(), iters=10, show=True)

      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env)
        print(episode_return)
        break
  i+=1
episode_return

-2.0
-22.0
1.0


1.0

### Creación del video

## Boxing v4 epocas y 1000 iteraciones ResNet

In [ ]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 701/702 [00:00<00:00, 2337.08it/s]


In [ ]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 600/601 [00:00<00:00, 1618.51it/s]


In [ ]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 700/701 [00:00<00:00, 1693.94it/s]


Dado el downsampling se tubo que reducir la resolucion de las imagenes

In [ ]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(80,100) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image.numpy(), dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 713/714 [00:00<00:00, 4190.19it/s]


Intento de usar la imagen antes de hacer downsampling, ya que como se vio anteriormente el resizing comprometio la resolucion

In [ ]:
episode_return=0.0
i=0
while episode_return < 1:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, im = env_step(env, action[0].numpy(), iters=10, show=False)
      images.append(im[-1])
      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env)
        print(episode_return)
        break
  i+=1
episode_return

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  # Remove the CWD from sys.path while we load stuff.


-55.0
-50.0
1.0


1.0

In [ ]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image, dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 713/714 [00:00<00:00, 1633.40it/s]


#Segunda Simulacion Unet

### Simulación

In [ ]:
episode_return=0.0
i=0
while episode_return < 1:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, _ = env_step(env, action[0].numpy(), iters=10, show=True)

      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env)
        print(episode_return)
        break
  i+=1
episode_return

## Boxing v4 10 epocas y 1000 iteraciones UNet

In [ ]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 714/715 [00:00<00:00, 1669.28it/s]


#Simulaciones Para diferentes juegos de atari

###Solaris

In [ ]:
episode_return=0.0
i=0
while episode_return < 100:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, im = env_step(env, action[0].numpy(), iters=10, show=False)
      images.append(im[-1])
      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env,10)
        print(episode_return)
        break
  observation = env_reset(env,10)
  print(episode_return)
  i+=1
episode_return

0.0
0.0
0.0
0.0
1400.0


1400.0

In [ ]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image, dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 720/721 [00:00<00:00, 1551.48it/s]


###PrivateEye

In [19]:
episode_return=0.0
i=0
while episode_return < 100:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, im = env_step(env, action[0].numpy(), iters=10, show=False)
      images.append(im[-1])
      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env,10)
        print(episode_return)
        break
  observation = env_reset(env,10)
  print(episode_return)
  i+=1
episode_return

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  # Remove the CWD from sys.path while we load stuff.


100.0


100.0

In [20]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image, dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)3612672/45929032 bytes (7.9%)7815168/45929032 bytes (17.0%)12083200/45929032 bytes (26.3%)16318464/45929032 bytes (35.5%)20512768/45929032 bytes (44.7%)24764416/45929032 bytes (53.9%)29024256/45929032 bytes (63.2%)33226752/45929032 bytes (72.3%)37543936/45929032 bytes (81.7%)41828352/45929032 bytes (91.1%)45929032/45929032 bytes (100.0%)
  Done
File saved as /root/.imageio/ffmpeg/ffmpeg-linux64-v3.3.1.


100%|█████████▉| 720/721 [00:00<00:00, 2454.92it/s]


###Frostbite

In [36]:
episode_return=0.0
i=0
while episode_return < 150:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, im = env_step(env, action[0].numpy(), iters=10, show=False)
      images.append(im[-1])
      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env,10)
        print(episode_return)
        break
  observation = env_reset(env,10)
  print(episode_return)
  i+=1
episode_return

110.0
110.0
180.0
180.0


180.0

In [32]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image, dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 349/350 [00:00<00:00, 2029.91it/s]


In [37]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image, dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 365/366 [00:00<00:00, 2029.24it/s]


###CrazyClimber

In [41]:
episode_return=0.0
i=0
while episode_return < 150:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, im = env_step(env, action[0].numpy(), iters=10, show=False)
      images.append(im[-1])
      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env,10)
        print(episode_return)
        break
  observation = env_reset(env,10)
  print(episode_return)
  i+=1
episode_return

0.0
0.0
0.0
0.0
100.0
0.0
100.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
200.0


200.0

In [42]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image, dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 720/721 [00:00<00:00, 2499.35it/s]


###Bowling

Extrañamente se minimizo el reward en el entrenamiento y no se porque. Aunque supongo que eso demuestra de que tiene un efecto.

In [54]:
episode_return=0.0
i=0
while episode_return < 1:
  observation, episode_return, episode_length = env_reset(env,10), 0, 0
  images = []
  for t in range(steps_per_epoch):
      # Get the logits, action, and take one step in the environment
      logits, action = sample_action(observation.reshape((1,observation.shape[0],observation.shape[1],observation.shape[2])))
      observation_new, reward, done, im = env_step(env, action[0].numpy(), iters=10, show=False)
      images.append(im[-1])
      episode_return += reward

      # Update the observation
      observation = observation_new

      # Finish trajectory if reached to a terminal state
      if done:
        observation = env_reset(env,10)
        print(episode_return)
        break
  observation = env_reset(env,10)
  print(episode_return)
  i+=1
episode_return

0.0
0.0
0.0
0.0
0.0
0.0
1.0


1.0

In [55]:
import cv2
from moviepy.editor import *

def create_video(images, filename):
  res=(160,210) #resulotion
  out = cv2.VideoWriter(filename,cv2.VideoWriter_fourcc('M','J','P','G'), 10, res)
  for image in images:
      image=np.array(image, dtype=np.uint8)
      out.write(image)

  out.release()
  return VideoFileClip(filename)

clip=create_video(images, "tmp.avi")
clip.ipython_display(width=400,maxduration=120)

100%|█████████▉| 720/721 [00:00<00:00, 2952.35it/s]
